# KNN

## Curso "Introducción al Aprendizaje Automático"
## Facultad de Ingeniería
## UdelaR
fasdfasdfajsdfnsd

K-Nearest Neighbors (KNN) es un modelo sencillo e intuitivo de aprendizaje supervisado. Clasifica una instancia nueva observando a qué clase pertenecen sus k vecinos más cercanos en el conjunto de entrenamiento, asumiendo que los ejemplos similares tienden a compartir la misma etiqueta.

In [ ]:
%pylab inline
import IPython
import sklearn as sk
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt


print('IPython version:', IPython.__version__)
print('numpy version:', np.__version__)
print('scikit-learn version:', sk.__version__)
print('pandas version:', pd.__version__)
print('matplotlib version:', matplotlib.__version__)

Populating the interactive namespace from numpy and matplotlib
IPython version: 7.34.0
numpy version: 2.0.2
scikit-learn version: 1.6.1
pandas version: 2.2.2
matplotlib version: 3.10.0


# Importar el dataset

Vamos a usar el dataset con personajes de los Simpsons que usamos en el practico pasado, similar al que vimos en clase. Son datos sinteticos, de manera que puede contener errores.


La siguiente celda puede que no ejecute bien si corren localmente. Pueden descargar el archivo manualmente desde [este enlace](https://docs.google.com/spreadsheets/d/1nmBmgnPlkSyx8nsRKQAnBtkjIqIjEPTmxiX0dMvEADE/edit?usp=sharing)

In [ ]:
dataset_url ="https://drive.google.com/file/d/1mvvP2S0ltwFHOwluGn-zha2Ga3Kn3bPv/view?usp=sharing"

!pip install -q gdown

import gdown


# Use gdown to download
gdown.download(dataset_url, output=None, quiet=False, fuzzy=True)

Downloading...
From: https://drive.google.com/uc?id=1mvvP2S0ltwFHOwluGn-zha2Ga3Kn3bPv
To: /content/toy_dataset.csv
100%|██████████| 9.95k/9.95k [00:00<00:00, 3.46MB/s]


'toy_dataset.csv'

La siguiente celda la ejecutamos para validar que el archivo este en el lugar adecuado:

In [ ]:
import os

# assert <condicion que deberia cumplirse>, "mensaje de error si la condicion anterior falla"
assert os.path.exists("toy_dataset.csv"), "El archivo no existe"

Leemos el csv, para esto vamos a usar `Pandas`: es una gran biblioteca para analisis de datos, no vamos a profundizar demasiado en ella en el curso.

In [ ]:
import pandas as pd

df = pd.read_csv("toy_dataset.csv")  # df es un DataFrame, muy similar a los de R

Cargamos todas las features que desarrollamos la clase pasada, y separamos en train/testustilizando los mismos parametros:

_Nota: si uds desarrollaron alguna más que quieran agregar, pueden hacerlo!_

In [ ]:
from sklearn.model_selection import train_test_split
# dejamos libre el # de columnas a mostraren un DataFrame, para verlas todas
pd.set_option('display.max_columns', None)

# Casteamos features booleanas
def str_to_bool(x):
  return x.strip().lower() != "no"

boolean_features = ['Tiene barba', 'Tiene bigote', 'Usa collar', 'Usa lentes', 'Usa caravanas', 'Usa corbata', 'Usa moño','Usa chupete', 'Es fumador']
target = "Personaje principal"

for c in boolean_features + [target]:
  df[c] = df[c].apply(str_to_bool)

# Agreagamos todas las features que se calcular a partir solamente de la instancia
def se_apellida_simpson(nombre):
  return "simpson" in nombre.lower()

df["apellido_simpson"] = df["Nombre"].apply(se_apellida_simpson)
# Creamos una nueva columna: para cada fila, calculamos el cociente entre las apariciones en especiales y las apariciones totales
df["ratio_especiales"] = df["Apariciones en especiales"] / (df["Apariciones"]+1e-7)
df["tiene_vello_facial"] = (df["Tiene bigote"] | df["Tiene barba"])
df["aparece_mas_de_30"] = df["Apariciones"] > 30
df["ultimo_episodio"] = df["Primer episodio"] + df["Apariciones"]

# Partimos el dataset en train/test
X = df.drop("Personaje principal", axis=1)
y = df["Personaje principal"]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y, shuffle=True)

max_apariciones = X_train["Apariciones"].max()
X_train["apariciones_normalizadas"] =  X_train["Apariciones"] / max_apariciones
X_test["apariciones_normalizadas"] =  X_test["Apariciones"] / max_apariciones

max_1er_ep = X_train["Primer episodio"].max()
X_train["1er_ep_normalizado"] =  X_train["Primer episodio"] / max_1er_ep
X_test["1er_ep_normalizado"] =  X_test["Primer episodio"] / max_1er_ep

# calculamos las apariciones_por_episodio (ex "feature cinco")
ultimo_episodio = X_train["ultimo_episodio"].max() #
X_train["apariciones_por_episodio"] = X_train["Apariciones"] / (ultimo_episodio + 1 - X_train["Primer episodio"])
X_test["apariciones_por_episodio"] = X_test["Apariciones"] / (ultimo_episodio + 1 - X_test["Primer episodio"])


X_train.head()

Agregamos el encoding de las features ordinales y one-hot:

In [ ]:
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder

categorical_features = ['Sexo', 'Pelo', 'Color de piel',
                          'Color de pelo']


numerical_features = ['Edad', 'Tiene barba', 'Tiene bigote', 'Usa collar',
                        'Usa lentes', 'Usa caravanas', 'Usa corbata', 'Usa moño',
                        'Usa chupete','Es fumador', 'Primer episodio', 'Apariciones',
                        'Apariciones en especiales', 'apellido_simpson',
                        'ratio_especiales',
       'tiene_vello_facial', 'aparece_mas_de_30', 'ultimo_episodio',
       'apariciones_normalizadas', '1er_ep_normalizado',
       'apariciones_por_episodio']

ordinal_features = ['Grupo Etario']



# Aplicar One-Hot Encoding a las características categóricas
# Creamos una instancia del OneHotEncoder
ohe_encoder = OneHotEncoder(handle_unknown='ignore', sparse_output=False)

# Entrenamos el encoder con los datos de entrenamiento
ohe_encoder.fit(X_train[categorical_features])

# Transformamos los datos de entrenamiento y prueba
X_train_categorical_encoded = ohe_encoder.transform(X_train[categorical_features])
X_test_categorical_encoded = ohe_encoder.transform(X_test[categorical_features])


# Initialize the OrdinalEncoder with the specified order
oe = OrdinalEncoder(categories=[['Joven','Adulto', 'Adulto mayor']],
                    handle_unknown="use_encoded_value",unknown_value=-1)

X_train_ordinal = oe.fit_transform(X_train[ordinal_features])
X_test_ordinal = oe.transform(X_test[ordinal_features])

# Obtenemos los nombres de las nuevas columnas creadas por el OneHotEncoder
new_categorical_feature_names = ohe_encoder.get_feature_names_out(categorical_features)

# Creamos DataFrames con las características categóricas codificadas
X_train_categorical_df = pd.DataFrame(X_train_categorical_encoded,
                                      columns=new_categorical_feature_names,
                                      index=X_train.index)
X_test_categorical_df = pd.DataFrame(X_test_categorical_encoded,
                                     columns=new_categorical_feature_names,
                                     index=X_test.index)

X_train_ordinal = pd.DataFrame(X_train_ordinal, columns=['grupo etario_encoded'], index=X_train.index)
X_test_ordinal = pd.DataFrame(X_test_ordinal, columns=['grupo etario_encoded'], index=X_test.index)

# Concatenamos las características numéricas originales con las categóricas codificadas
X_train_processed = pd.concat([X_train[numerical_features], X_train_categorical_df, X_train_ordinal], axis=1)
X_test_processed = pd.concat([X_test[numerical_features], X_test_categorical_df, X_test_ordinal], axis=1)


A partir de acá, vamos a trabajar con `X_train_processed`y `X_test_processed`, que contiene los mismos datos de la clase pasada:

In [ ]:
X_train_processed.shape, X_test_processed.shape

((70, 42), (18, 42))

Comencemos por ver las correlacioenes que tenemos entre nuestras columnas

In [ ]:
pd.concat([y_train, X_train_processed], axis=1).corr('pearson')

## Ejercicio:
- Entre el target (`"Personaje principal"`) y `"Edad"` hay una correlación de `-0.056`: qué implica?
- La correlación entre las variables `Sexo_Masculino` y `Sexo_Femenino` vale -1, mientras que entre las variables `Pelo_corto` y `Pelo_calvo` es 0.114: a qué se debe?
- Qué variable es la más prometedora? Justifique brevemente
- Eliminaria alguna variable en este punto? Cual(es)? Justifique brevemente
- En clase mencionamos la heuristica que proponen [Duda et.al](https://books.google.com.uy/books/about/Pattern_Classification.html?id=YoxQAAAAMAAJ&source=kp_book_description&redir_esc=y): $N>=5 \times d$, donde $N$ es la cantidad de datos disponibles y $d$ las dimensiones de su representación. Cuántas columnas deberíamos seleccionar, como maximo, en este problema?


# Entrenar nuestro primer KNN

Comencemos por entrenar nuestro primer knn, usaremos todos los atributos y todos los parametros por defecto:

In [ ]:
from sklearn.neighbors import KNeighborsClassifier

knn = KNeighborsClassifier()
knn.fit(X_train_processed, y_train)

KNeighborsClassifier()

In [ ]:
from sklearn.model_selection import cross_val_score

# Perform cross-validation with 7 folds
cv_scores = cross_val_score(knn, X_train_processed, y_train, cv=7, scoring="f1")

print("Results with defaults:")
print(f"F-score: {cv_scores.mean():0.3f}±{cv_scores.std():0.3f}")

## Normalizar

Veamos el efecto de normalizar. Para esto, normalizamos segun las dos estrategias que comentamos en clase: `MinMaxScaler, StandardScaler`.

Evaluaos cada una de ellas al usar knn con los parametros por defecto, y las evaluamos con valizacion cruzada, a ver cual resulta mejor:

In [ ]:
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from sklearn.model_selection import cross_val_score

# MinMax Scaling
scaler_minmax = MinMaxScaler()
X_train_minmax = scaler_minmax.fit_transform(X_train_processed)
X_test_minmax = scaler_minmax.transform(X_test_processed)

# Standardization (Mean 0, Std 1)
scaler_std = StandardScaler()
X_train_std = scaler_std.fit_transform(X_train_processed)
X_test_std = scaler_std.transform(X_test_processed)

# Train KNN with default parameters using MinMax Scaled data
knn_minmax = KNeighborsClassifier()
cv_scores_minmax = cross_val_score(knn_minmax, X_train_minmax, y_train, cv=7, scoring="f1")

print("Results with MinMax Scaling:")
print(f"F-score: {cv_scores_minmax.mean():0.3f}±{cv_scores_minmax.std():0.3f}")
print("-" * 20)

# Train KNN with default parameters using Standardized data
knn_std = KNeighborsClassifier()
cv_scores_std = cross_val_score(knn_std, X_train_std, y_train, cv=7, scoring="f1")

print("Results with Standardization:")
print(f"F-score: {cv_scores_std.mean():0.3f}±{cv_scores_std.std():0.3f}")

## Ejercicio:
Replique el codigo de la celda anterior, pero, en vez de usar `KNNClassifier` utilice `DecisionTreeClassifier(criterion="entropy", random_state=0)`.

Que resultados observa? A que se debe?

_sugerencia: formulen una hipotesis de qué esperan que pasen antes de ejecutar el experimento_

In [ ]:
from sklearn.tree import DecisionTreeClassifier
...

# Feature selection

## SlectKBest
Probemos elegir las mejores 14 features, mirando unicamente la relacion lineal con el target:

In [ ]:
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif

# Usamos f_classif que mide la dependencia lineal entre features y el target
# Aunque no es correlación exacta, es una medida de la relación lineal.
# Seleccionamos las 14 mejores características
selector = SelectKBest(score_func=f_classif, k=14)

# Ajustamos el selector a los datos de entrenamiento y el target
selector.fit(X_train_processed, y_train)

# Obtenemos las columnas seleccionadas (indices booleanos)
selected_features_mask = selector.get_support()

# Obtenemos los nombres de las columnas seleccionadas
selected_feature_names = X_train_processed.columns[selected_features_mask]

# Transformamos los datos de entrenamiento y prueba para quedarnos solo con las features seleccionadas
X_train_selected_k = selector.transform(X_train_processed)
X_test_selected_k = selector.transform(X_test_processed)

print("Features seleccionadas:")
print(selected_feature_names)
print("\nDimensiones de los datos de entrenamiento después de la selección:", X_train_selected.shape)
print("Dimensiones de los datos de prueba después de la selección:", X_test_selected.shape)

In [ ]:
knn_k_best = KNeighborsClassifier()
cv_scores_k_best = cross_val_score(knn_k_best, X_train_selected_k, y_train, cv=7, scoring="f1")

print("Results with 14 best:")
print(f"F-score: {cv_scores_k_best.mean():0.3f}±{cv_scores_k_best.std():0.3f}")

## RFE: Recursive Feature Elimination
Probemos otro criterio: tomar las 14 mejores pero siguiendo RFE. Como KNN no tiene implementado un `feature_importance_`, usemos un árbol para estimar la importancia de las features. Veamos luego su performance.


### Ejercicio:
Supongamos que busco entrenar un modelo que si tiene un feature_importance (ejemplo: un arbol). Deberia usarlo tambien para hacer la seleccion de atributos? Justifique brevemente


In [ ]:
from sklearn.feature_selection import RFE

# Creamos un estimador base para RFE
# Usamos un DecisionTreeClassifier como estimador
estimator = DecisionTreeClassifier(random_state=42)

# Inicializamos RFE con el estimador y el número de features a seleccionar
# Seleccionamos las 14 mejores características
rfe = RFE(estimator=estimator, n_features_to_select=14)

# Ajustamos RFE a los datos de entrenamiento
# Esto realizará iterativamente la eliminación de features
rfe.fit(X_train_processed, y_train)

# Obtenemos las columnas seleccionadas (indices booleanos)
selected_features_mask_rfe = rfe.support_

# Obtenemos los nombres de las columnas seleccionadas por RFE
selected_feature_names_rfe = X_train_processed.columns[selected_features_mask_rfe]

# Transformamos los datos de entrenamiento y prueba para quedarnos solo con las features seleccionadas
X_train_selected_rfe = rfe.transform(X_train_processed)
X_test_selected_rfe = rfe.transform(X_test_processed)

print("Features seleccionadas por RFE:")
print(selected_feature_names_rfe)
print("\nDimensiones de los datos de entrenamiento después de RFE:", X_train_selected_rfe.shape)
print("Dimensiones de los datos de prueba después de RFE:", X_test_selected_rfe.shape)

# Evaluamos la performance con las features seleccionadas por RFE usando KNN
knn_rfe = KNeighborsClassifier()
cv_scores_rfe = cross_val_score(knn_rfe, X_train_selected_rfe, y_train, cv=7, scoring="f1")

print("\nResults with RFE (14 features):")
print(f"F-score: {cv_scores_rfe.mean():0.3f}±{cv_scores_rfe.std():0.3f}")

In [ ]:
selected_feature_names_rfe = set(selected_feature_names_rfe)
selected_feature_names =set(selected_feature_names)

print("Features seleccionadas:")
print(f"- por ambos: {selected_feature_names_rfe.intersection(selected_feature_names)}")
print(f"- solo por SelectKBest: {selected_feature_names.difference(selected_feature_names_rfe)}")
print(f"- solo por RFE: {selected_feature_names_rfe.difference(selected_feature_names)}")

## Sequencial Feature Elimination
Probemos por ultimo utilizando SFE para tomar las mejores 14 features.

Para hacerlo de manera mas eficiente, deberiamos usar `forward` o `backward`? Justifique y modifique el parametro `forward=True|False` segun corresponda.



In [ ]:
from sklearn.feature_selection import SequentialFeatureSelector

# Inicializamos el estimador base (KNN en este caso)
estimator = KNeighborsClassifier()

# Inicializamos SequentialFeatureSelector
# n_features_to_select=14: seleccionamos las 14 mejores features
# direction='completar aca': usen el metodo que use menos computo ('forward', 'backward)
# cv=7: usamos 7-fold cross-validation para evaluar cada subset de features
# scoring='f1': usamos F1-score como métrica de evaluación
sfs = SequentialFeatureSelector(estimator=estimator,
                                n_features_to_select=14,
                                direction='completar aca',  # 'forward', 'backward
                                cv=7,
                                scoring='f1',
                                n_jobs=-1)

# Ajustamos el SFS a los datos de entrenamiento
# Esto realiza la selección de features secuencialmente
sfs.fit(X_train_processed, y_train)

# Obtenemos las columnas seleccionadas (indices booleanos)
selected_features_mask_sfs = sfs.get_support()

# Obtenemos los nombres de las columnas seleccionadas por SFS
selected_feature_names_sfs = X_train_processed.columns[selected_features_mask_sfs]

# Transformamos los datos de entrenamiento y prueba para quedarnos solo con las features seleccionadas
X_train_selected_sfs = sfs.transform(X_train_processed)
X_test_selected_sfs = sfs.transform(X_test_processed)

print("Features seleccionadas por SequentialFeatureSelector (forward):")
print(selected_feature_names_sfs)
print("\nDimensiones de los datos de entrenamiento después de SFS:", X_train_selected_sfs.shape)
print("Dimensiones de los datos de prueba después de SFS:", X_test_selected_sfs.shape)

# Evaluamos la performance con las features seleccionadas por SFS usando KNN
# Aunque SFS ya utiliza CV internamente para seleccionar las features,
# podemos evaluar el modelo final con CV en el conjunto seleccionado
knn_sfs = KNeighborsClassifier()
cv_scores_sfs = cross_val_score(knn_sfs, X_train_selected_sfs, y_train, cv=7, scoring="f1")

print("\nResults with SFS (14 features, forward):")
print(f"F-score: {cv_scores_sfs.mean():0.3f}±{cv_scores_sfs.std():0.3f}")


## KNN hyperparams

Hasta ahora hemos dejados los hiperparametros de knn, y con eccos obtuvimos una forma de normalizar y seleccionar atributos que nos retrnan buenos resultados. Ahora podemos enfocarnos en mejorar los hiperparametros de knn.

Comencemos por vel el valor adecuado para K.

### Ejercicio:
- Qué pasa si k=1?
- Qué pasa si `k==len(X_train)`?

Justifique

In [ ]:
import matplotlib.pyplot as plt

# Determine the maximum value of k to test
max_k = int(len(X_train) / 7)
print(f"Testing k from 1 to {max_k}")

# Lists to store the results
k_values = []
mean_f1_scores = []
std_f1_scores = []

# Loop through k values from 1 to max_k
for k in range(1, max_k + 1):
  # Initialize KNN classifier with the current k
  knn = KNeighborsClassifier(n_neighbors=k)

  # Perform cross-validation with 7 folds
  cv_scores = cross_val_score(knn, X_train_selected_sfs, y_train, cv=7, scoring="f1", n_jobs=-1)

  # Store the results
  k_values.append(k)
  mean_f1_scores.append(cv_scores.mean())
  std_f1_scores.append(cv_scores.std())

  # Report f1 score for the current k
  print(f"k={k}: F-score = {cv_scores.mean():0.3f} ± {cv_scores.std():0.3f}")

# Plot the results
plt.figure(figsize=(12, 6))
plt.errorbar(k_values, mean_f1_scores, yerr=std_f1_scores, marker='o', linestyle='-', capsize=3)
plt.xlabel("Value of K for KNN")
plt.ylabel("Mean F1-score (Cross-validation)")
plt.title("KNN Performance (F1-score) vs. K Value")
plt.grid(True)
plt.xticks(k_values)
plt.show()


## Ejercicio:

Expanda la siguiente grilla de parametros para buscar los mejores.

_sugerencia: consultar la documentacion (`KNeighborsClassifier?`)_

In [ ]:
from sklearn.model_selection import GridSearchCV


# Definimos los parámetros a probar en la Grid Search
param_grid = {
    'n_neighbors': [10],  #
    'weights': ['uniform'],
    'metric': ['l1', 'l2', 'cosine']
}

# Creamos una instancia del clasificador KNN
knn = KNeighborsClassifier()

# Creamos una instancia de GridSearchCV
# estimator: el modelo a optimizar
# param_grid: el diccionario de parámetros a probar
# cv: número de folds para cross-validation
# scoring: la métrica a optimizar ('f1' para F1-score)
# n_jobs=-1: usa todos los núcleos disponibles
grid_search = GridSearchCV(estimator=knn,
                           param_grid=param_grid,
                           cv=7,
                           scoring='f1',
                           n_jobs=-1)

# Ejecutamos la Grid Search en los datos de entrenamiento finales
grid_search.fit(X_train_selected_sfs, y_train)

# Obtenemos los mejores parámetros encontrados
best_params = grid_search.best_params_

# Obtenemos el mejor score (media de F1-score en cross-validation)
best_score = grid_search.best_score_

# Calculamos el error estándar de la mejor configuración (aproximación usando los resultados de CV)
# sklearn.model_selection.GridSearchCV.cv_results_['std_test_score'][grid_search.best_index_]
std_best_score = grid_search.cv_results_['std_test_score'][grid_search.best_index_]


print("\nResultados de la Grid Search:")
print("Mejores parámetros encontrados:")
print(best_params)
print("\nMejor score (Media F1-score en CV) con los mejores parámetros:")
print(f"F-score: {best_score:0.3f}±{std_best_score:0.3f}")

## Vecindario definido segun distancia

Vamos a usar `RadiusNeighborsClassifier`

### Ejercicio:
- Que sucede si utilizo un valor demasiado bajo del radio? (_pista: estamos usando el parametro `outer_label`, consultar en documentación_)
- Que sucede si utilizo un valor demasiado alto del radio?
- Ejecute la siguiente celda: cual es el valor óptimo de `radius`? Cuál es el valor máximo (aproximadamente) para `radius`? (_pista: modifiquen los valores dados para ver como cambia el comportamiento_)

In [ ]:
import matplotlib.pyplot as plt
from sklearn.neighbors import RadiusNeighborsClassifier

# Define the radii to test
radii_to_test = range(100, 1000, 50)  # Valores desde el 100 al 1000, incrementando de a 50

# Lists to store the results
radii_values = []
mean_f1_scores_rnn = []
std_f1_scores_rnn = []

# Loop through radius values
for radius in radii_to_test:
  # Initialize RadiusNeighborsClassifier
  rnn = RadiusNeighborsClassifier(radius=radius, outlier_label="most_frequent", metric='l1', weights='uniform')

  # Perform cross-validation with 7 folds on the pre-processed data
  cv_scores_rnn = cross_val_score(rnn, X_train_processed, y_train, cv=7, scoring="f1", n_jobs=-1)

  # Store the results
  radii_values.append(radius)
  mean_f1_scores_rnn.append(cv_scores_rnn.mean())
  std_f1_scores_rnn.append(cv_scores_rnn.std())

  # Report f1 score for the current radius
  print(f"Radius={radius}: F-score = {cv_scores_rnn.mean():0.3f} ± {cv_scores_rnn.std():0.3f}")

# Plot the results
plt.figure(figsize=(12, 6))
plt.errorbar(radii_values, mean_f1_scores_rnn, yerr=std_f1_scores_rnn, marker='o', linestyle='-', capsize=3)
plt.xlabel("Value of Radius for RadiusNeighborsClassifier")
plt.ylabel("Mean F1-score (Cross-validation)")
plt.title("RadiusNeighborsClassifier Performance (F1-score) vs. Radius Value")
plt.grid(True)
plt.show()

#  ¿Podríamos haber tomado otras decisiones?
Hasta ahora, seguimos una secuencia de pasos razonable: primero elegimos la mejor normalización (manteniendo los demás parámetros fijos), luego seleccionamos la mejor estrategia para reducir a 14 atributos (sobre esa normalización), y por último, buscamos los mejores hiperparámetros para KNN.

## Ejercicio:

¿Creen que esta forma de avanzar garantiza encontrar la mejor combinación posible?
¿En qué puntos podríamos haber hecho las cosas de otra manera o de forma más completa?

Justifique brevemente

# Pipelines!

Un Pipeline en scikit-learn nos permite encadenar múltiples pasos del procesamiento de datos (como escalado, selección de atributos, y entrenamiento del modelo) en un único objeto. Esto facilita la organización del código, evita errores comunes y mejora la reproducibilidad de los experimentos.

¿Por qué usar Pipelines?
📦 Todo en uno: Agrupan preprocesamiento, selección de atributos y modelado en un solo flujo.

🔄 Facilita la validación cruzada: Nos aseguramos de que todos los pasos se hagan dentro de cada partición de la validación, evitando fugas de información (data leakage).

🔍 Permiten búsqueda de hiperparámetros conjunta: Se puede hacer búsqueda automática (GridSearchCV, RandomizedSearchCV) sobre todas las partes del pipeline, no solo sobre el modelo final.

✅ Reproducible y ordenado: Hace que todo el flujo de procesamiento y entrenamiento sea más claro, robusto y replicable.

In [ ]:
from sklearn.pipeline import Pipeline

# Based on the analysis, the best approach was:
# 1. Normalization: StandardScaler (Standardization)
# 2. Feature Selection: SequentialFeatureSelector (SFS forward, selecting 14 features)
# 3. KNN Hyperparameters: Based on the grid search and K value analysis.
#    Let's pick the best found from the grid search, which was n_neighbors=10, weights='uniform', metric='l1'.
#    Note: The K value plot suggested higher values might be better depending on the trade-off with variance.
#    Let's use the best parameters found by GridSearchCV on the SFS-selected features: best_params

# Define the steps of the pipeline
# Step 1: Standardization (applied before SFS)
# Step 2: Sequential Feature Selection (applied after scaling)
# Step 3: KNN Classifier with optimized hyperparameters
pipeline_steps = [
    ('scaler', StandardScaler()),  # Normalization found to be best or comparable
    ('feature_selection', SequentialFeatureSelector(estimator=KNeighborsClassifier(),
                                                    n_features_to_select=14,
                                                    direction='forward',
                                                    cv=7,
                                                    scoring='f1',
                                                    n_jobs=1)), # SFS as feature selection
    ('knn', KNeighborsClassifier(**best_params)) # KNN with best found hyperparameters
]

# Create the pipeline
best_pipeline = Pipeline(pipeline_steps)

cv_scores_sfs = cross_val_score(best_pipeline, X_train_processed, y_train, cv=7, scoring="f1", n_jobs=-1)

print("\nResults with SFS (14 features, forward):")
print(f"F-score: {cv_scores_sfs.mean():0.3f}±{cv_scores_sfs.std():0.3f}")


### Ejercicio: por qué demora tanto?!
Si estamos corriendo el miso pipe que hasta ahora, pero todo junto, por qué está tardando tanto esta celda? Qué implicancias tiene?

## Busqueda de hyperparametros en Pipes
El objeto `Pipeline` es tambien un estimador, y como tal podemos buscar hiperparametros.

El ejemplo de abajo muestra como hacerlo.

### Ejercico
Ejecutar la celda de abajo (toma algunos minutos).

Registrar la mejor configuración y los resultados.

Hacer una copia de la celda y re-ejecutar la busqueda de hiperparametros, siguiendo Grid o Random search para buscar una mejor connfiguración.

_Cuidado: como vimos, el pipeline demora más en ejecutar, de manera que hacer pruebas validando cada punto del pipe es también costoso._

In [ ]:
pipeline = Pipeline([
    ('scaler', StandardScaler()), # Placeholder, will be replaced by scaler in param_grid
    ('feature_selection', SelectKBest()), # Placeholder for feature selection method
    ('knn', KNeighborsClassifier(weights='uniform'))
])

# Definir el espacio de búsqueda de parámetros para GridSearchCV
param_grid = {
    # Estrategias de estandarización: MinMaxScaler o StandardScaler
    'scaler': [MinMaxScaler(), StandardScaler()], # None para no probar nada

    # Estrategias de selección de features: SelectKBest, RFE, SequentialFeatureSelector
    'feature_selection': [
        SelectKBest(k=7,score_func=f_classif),
        RFE(n_features_to_select=7, estimator=DecisionTreeClassifier(random_state=42), step=1), # Estimador para RFE, step=1 elimina una feature por iteración
        SequentialFeatureSelector(n_features_to_select=7, estimator=KNeighborsClassifier(), direction='forward', cv=7, scoring='f1', n_jobs=1), # Estimador para SFS
    ],

    # Parámetros del clasificador KNN
    'knn__n_neighbors': [3, 5, 7], # Cantidad de vecinos a usar
    # 'knn__weights': ['uniform', 'distance'], # Peso de los vecinos
    # 'knn__metric': ['euclidean', 'manhattan', "cosine"] # Métrica de distancia
}

grid_search_pipeline = GridSearchCV(estimator=pipeline,
                                    param_grid=param_grid,
                                    cv=7,
                                    scoring='f1',
                                    n_jobs=-1, # Usar todos los cores para las combinaciones externas
                                    verbose=2) # Para ver el progreso

# Ejecutamos la Grid Search en los datos de entrenamiento procesados (antes de la normalización y selección)
# El pipeline se encargará de aplicar la normalización y la selección dentro de cada fold de CV.
grid_search_pipeline.fit(X_train_processed, y_train)

# Obtenemos los mejores parámetros encontrados
best_params_pipeline = grid_search_pipeline.best_params_

# Obtenemos el mejor score (media de F1-score en cross-validation)
best_score_pipeline = grid_search_pipeline.best_score_

# Calculamos el error estándar de la mejor configuración
std_best_score_pipeline = grid_search_pipeline.cv_results_['std_test_score'][grid_search_pipeline.best_index_]


print("\nResultados de la Grid Search sobre el Pipeline:")
print("Mejores parámetros encontrados:")
print(best_params_pipeline)
print("\nMejor score (Media F1-score en CV) con los mejores parámetros:")
print(f"F-score: {best_score_pipeline:0.3f}±{std_best_score_pipeline:0.3f}")

In [ ]:
# copien aca la celda anterior y modifiquenla segun crean conveniente.
# El objetivo en este punto es encontrar los mejores valores posibles

# Hora del Test-set!
Hora de la evaluacion final!

- Instanciar el mejor modelo logrado hasta el momento, con los mejores parametros
- Entrenarlo con todos los datos de entrenamiento
- Predecir sobre el conjunto de test

In [ ]:

best_model = grid_search_pipeline.best_estimator_

best_model.fit(X_train_processed, y_train)
y_pred = best_model.predict(X_test_processed)

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(y_test, y_pred))

Por ultimo vemos la matriz de confusion:

In [ ]:
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix
import seaborn as sns

# Generate the confusion matrix
cm = confusion_matrix(y_test, y_pred)

# Plot the confusion matrix
plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt='d', cmap='Blues')
plt.xlabel('Predicted')
plt.ylabel('Actual')
plt.title('Confusion Matrix')
plt.show()

## Ejercicio
Compare la performance obtenida por validación cruzada para